<script>
    var code_show=true; //true -> hide code at first

    function code_toggle() {
        $('div.prompt').hide(); // always hide prompt

        if (code_show){
            $('div.input').hide();
        } else {
            $('div.input').show();
        }
        code_show = !code_show
    }
    $( document ).ready(code_toggle);
</script>

<a href="javascript:code_toggle()">[Toggle Code]</a>

## SF Crime, Summer of 2014

Ah, San Francisco, the beautiful city by the bay. A city that is reknown for its statuure as the tech hotbed and the cultural capital of the west coast.  But crimes happen here, too you know.  Well, there was that zodiac killer, but other than that, we tend not to hear too much about crimes in SF.  Alas, that doesn't mean it's always lovey dovey in SF.

In this exercise, we are going to look at the SF's crime statistics from summer of 2014.  In my opinon, it would silly trying to make statistical assertion based on the baseline dataset.  Too much efforts would be required to obtain ancillary data to make any meaningful correlationships.  Instead, we are going to visualize this dataset and detect temporal and spacial patterns.  Specifically, we have the following questions that we like to get answers for:

#### Crime by the PD District
1. how do the crime rates spread across different neighborhoods (in our case PD Districts?)
2. within each district, what is the break-down for different types of crimes?

#### Car break-in's
1. what time of the day do car break-ins happen most often?
2. how can we get a glimpse of the car break-ins spacially?  Where do they occur most often?
3. does the day of the week make any difference in terms of car break-ins?

In [3]:
import graphlab as gl
import graphlab.aggregate as agg

#gl.product_key.set_product_key('6E19-9A71-9128-0AD3-AA0C-8C21-8919-1180')

gl.canvas.set_target('ipynb') # output a single GraphLab Canvas view to a IPython Notebook cell

import pandas as pd
import numpy as np

A newer version of GraphLab Create (v1.8.1) is available! Your current version is v1.7.1.

You can use pip to upgrade the graphlab-create package. For more information see https://dato.com/products/create/upgrade.


In [4]:
from __future__ import print_function

from bokeh.charts import Bar, output_notebook, output_file, show
from bokeh.charts.attributes import cat, color
from bokeh.charts.operations import blend
from bokeh.plotting import reset_output, show, output_notebook, vplot

from bokeh.document import Document
from bokeh.embed import file_html

from bokeh.models.widgets.layouts import VBoxForm
from bokeh.models.glyphs import Circle
from bokeh.models import (
    GMapPlot, Range1d, ColumnDataSource,
    PanTool, WheelZoomTool, BoxSelectTool,
    GMapOptions,
    ColumnDataSource, Plot, Circle, Range1d, 
    LinearAxis, HoverTool, Text,
    SingleIntervalTicker, Slider, CustomJS
)

from bokeh.resources import INLINE, JSResources
from bokeh.palettes import Spectral10, Spectral7, Purples9
from IPython.display import display, HTML
from jinja2 import Template
from bokeh.io import output_file, output_notebook, show, vform

# find what version of bokeh, issue cmd "bokeh.__version__"

[INFO] 1454099461 : INFO:     (initialize_globals_from_environment:282): Setting configuration variable GRAPHLAB_FILEIO_ALTERNATIVE_SSL_CERT_FILE to /Users/howard/anaconda/envs/dato-env/lib/python2.7/site-packages/certifi/cacert.pem
1454099461 : INFO:     (initialize_globals_from_environment:282): Setting configuration variable GRAPHLAB_FILEIO_ALTERNATIVE_SSL_CERT_DIR to 
This non-commercial license of GraphLab Create is assigned to studiocardo@gmail.com and will expire on November 14, 2016. For commercial licensing options, visit https://dato.com/buy/.

[INFO] Start server at: ipc:///tmp/graphlab_server-17319 - Server binary: /Users/howard/anaconda/envs/dato-env/lib/python2.7/site-packages/graphlab/unity_server - Server log: /tmp/graphlab_server_1454099461.log
[INFO] GraphLab Server Version: 1.7.1


In [5]:
sf = gl.SFrame.read_csv('./data/sanfrancisco_incidents_summer_2014.csv')

PROGRESS: Finished parsing file /Users/howard/Desktop/SH3.0/Coursera/UoW/Communicating-Data-Science-Results/SF-Crime/data/sanfrancisco_incidents_summer_2014.csv
PROGRESS: Parsing completed. Parsed 100 lines in 0.301423 secs.
------------------------------------------------------
Inferred types from first line of file as 
column_type_hints=[int,str,str,str,str,str,str,str,str,float,float,str,int]
If parsing fails due to incorrect types, you can correct
the inferred type list above and pass it to read_csv in
the column_type_hints argument
------------------------------------------------------
PROGRESS: Finished parsing file /Users/howard/Desktop/SH3.0/Coursera/UoW/Communicating-Data-Science-Results/SF-Crime/data/sanfrancisco_incidents_summer_2014.csv
PROGRESS: Parsing completed. Parsed 28993 lines in 0.265221 secs.


___
### Let's get a quick overlook of the SF crime statistics

In [6]:
sf_PdDistrict = sf.groupby(["PdDistrict"], {'Counts':gl.aggregate.COUNT()}).sort('Counts', ascending=False)

min=sf_PdDistrict['Counts'].min()
sf_PdDistrict['normalized']=sf_PdDistrict['Counts'].apply(lambda x: float(x)/min).apply(lambda x: round(x, 2))

sf_PdDistrict.sort('normalized', ascending=False)
sf_PdDistrict['normalized']

dtype: float
Rows: 10
[3.71, 2.39, 2.32, 2.27, 1.76, 1.54, 1.46, 1.2, 1.1, 1.0]

## Q. Crime Reports by PdDistrict and Category

First question we want to ask is *how do the crime stats from different PD Districts compare to each other*?  Which district has the highest crime reported?  And which one has the lowest?  

It would also be interesting to know:

1. Can we quickly and visually size up the difference in the number of crimes reported? 
2. **what** the major categories of crimes are **within each** PD District
3. are they all the same?  
4. Does one particular category stand out more in one district than the other? 


In [7]:
# 1. arrange by PdDistrict and then by Category

sf_PdDistrict_pd = sf.groupby(["PdDistrict",'Category'], {'Counts':gl.aggregate.COUNT()}).sort('Counts', ascending=False)

#
# convert SFrame to a Pandas DF so we can utilize the plotting utils
#
#sf_PdDistrict_pd = gl.SFrame.to_dataframe(sf_PdDistrict_pd)
sf_PdDistrict_pd

Columns:
	Category	str
	PdDistrict	str
	Counts	int

Rows: 265

Data:
+----------------+------------+--------+
|    Category    | PdDistrict | Counts |
+----------------+------------+--------+
| LARCENY/THEFT  |  SOUTHERN  |  2562  |
| LARCENY/THEFT  |  CENTRAL   |  1574  |
| LARCENY/THEFT  |  NORTHERN  |  1499  |
| LARCENY/THEFT  |  MISSION   |  671   |
|  NON-CRIMINAL  |  SOUTHERN  |  639   |
| LARCENY/THEFT  |    PARK    |  576   |
| LARCENY/THEFT  | INGLESIDE  |  548   |
| LARCENY/THEFT  |  TARAVAL   |  547   |
| OTHER OFFENSES |  SOUTHERN  |  543   |
|    ASSAULT     |  SOUTHERN  |  528   |
+----------------+------------+--------+
[265 rows x 3 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [8]:
### I found the top 5 categories and the remaining for all PdDistricts here and put them into a new SF called counts_sf

# Create an empty pandas DF
#
counts_sf = gl.SFrame()
sfpd = sf_PdDistrict['PdDistrict']

for p in sfpd:
    this_p = sf_PdDistrict_pd.filter_by(p, 'PdDistrict').sort('Counts', ascending=False)
    top5 = this_p.head(5)
    not_top5 = this_p['Counts'][5:len(this_p)].sum()
    other = gl.SFrame({'Category': ["OTHER"], 'PdDistrict': [p], 'Counts': [not_top5]})
    top5 = top5.append(other)
    counts_sf = counts_sf.append(top5)

counts_sf['Category'].unique()

dtype: str
Rows: 10
['VEHICLE THEFT', 'ASSAULT', 'NON-CRIMINAL', 'SUSPICIOUS OCC', 'OTHER OFFENSES', 'LARCENY/THEFT', 'DRUG/NARCOTIC', 'MISSING PERSON', 'OTHER', 'WARRANTS']

In [9]:
# Reduce the category variation of sf to what's in top_crimes

sf2 = sf

# Hacking it by hand... Can't work out this SFrame->SArray->list element removal

#True if x % 2 == 0 else False
#sf[sf['id'].apply(lambda x: math.log(x) <= 1)]

def changecrime(crime):
    top_crimes = ['VEHICLE THEFT', 'ASSAULT', 'NON-CRIMINAL', 'SUSPICIOUS OCC', 'LARCENY/THEFT', 'DRUG/NARCOTIC', 'MISSING PERSON', 'WARRANTS']
 
    if crime in top_crimes:
        return crime
    else:
        return "OTHER OFFENSES"

sf2['Category'] = sf2['Category'].apply(changecrime)
#sf2[sf2['Category'].apply(lambda x: x if x in top_crimes else "OTHER OFFENSES")]

sf2g = sf2.groupby('Category', {'Counts': agg.COUNT()}).sort('Counts', ascending=False)
sf2g
larceny = sf2[sf2['Category'] == "LARCENY/THEFT"]

llcool = larceny.groupby("PdDistrict", {'Counts': agg.COUNT()})
pdl = llcool.to_dataframe()
pdl.set_index(pdl['PdDistrict'])

top_crimes = ['VEHICLE THEFT', 'ASSAULT', 'NON-CRIMINAL', 'SUSPICIOUS OCC', 'LARCENY/THEFT', 'DRUG/NARCOTIC', 'MISSING PERSON', 'WARRANTS']

pdsf2 = pd.DataFrame(index=sfpd)
pdsf2 = pdsf2.sort(ascending=False)

/Users/howard/anaconda/envs/dato-env/lib/python2.7/site-packages/ipykernel/__main__.py:32: FutureWarning: sort(....) is deprecated, use sort_index(.....)


In [10]:
top_crimes = ['OTHER OFFENSES','VEHICLE THEFT', 'ASSAULT', 'NON-CRIMINAL', 'SUSPICIOUS OCC', 'LARCENY/THEFT', 'DRUG/NARCOTIC', 'MISSING PERSON', 'WARRANTS']

total = sf2.groupby("PdDistrict", {"TOTAL": agg.COUNT()}).sort('PdDistrict', ascending=False)
df_topcrimes = total.to_dataframe()
   
for crime in top_crimes:
    col = sf2[sf2['Category'] == crime].groupby("PdDistrict", {crime: agg.COUNT()}).sort('PdDistrict', ascending=False)
    pdcol = col.to_dataframe()
    pdcol.set_index(pdcol['PdDistrict'])
    pdcol
    df_topcrimes.loc[:,crime] = pdcol

#pdsf2 = pdsf2.sort_values("TOTAL", ascending=False)
df_topcrimes=df_topcrimes.sort_values("TOTAL", ascending=False)

In [11]:
# Make the plot
bar = Bar(df_topcrimes,
          values=blend('OTHER OFFENSES','VEHICLE THEFT', 'ASSAULT', 'NON-CRIMINAL', 'SUSPICIOUS OCC', 'LARCENY/THEFT', 'DRUG/NARCOTIC', 'MISSING PERSON', 'WARRANTS', name='Incidents', labels_name='Incident'),
          label=cat(columns='PdDistrict', sort=False),
          stack=cat(columns='Incident', sort=False),
          color=color(columns='Incident', palette=Spectral10, sort=False),
          legend='top_right',
          title="Crime Indident by PdDistrict",
          tooltips=[('Type: ', '@Incident')],
          plot_width = 900, plot_height=600
         )

# Local display w/n the notebook
output_notebook()
show(bar)

# Output to a file too
#reset_output()
#output_file('./output/crime_by_pddistrict.html')
#show(VBoxForm(bar))

BokehJS successfully loaded.

### So...

Base on this plot, we can conclude the following findings:

1. Southern PD District has the highest number of crimes reported.  It has roughtly 2000 more crime reported than the Mission (2nd place) and 4000 more than the last place, Richmond.

2. By far, the most crime reported in Southern PD District is related to Theft and Larceny, which occupies a considerably smaller portion of Mission's crime tally.  But for Northern and Central districts, Larceny/Theft are again the main culprit.  Theft and Larcy play a less important role in other districts, in terms of the overall percentage, except Park and Richmond.


___
## Q. Have your stuff stolen from your car

Everyone who's ever lived in a major city most likely has his/her car broken at least once or twice or many more time.  It's a part of the "privilege".

The general intuition suggests that the time of the day and the location where you park have a lot to do with the chance of getting your car broken in.  But is it *really* the case?  

Let's see if we can detect a pattern with the data.

In [40]:
def timegrp(time):
    breaks = ["00:00", "02:00", "04:00", "06:00", "08:00", "10:00", "12:00","14:00", "16:00", "18:00", "20:00", "22:00", "24:00"]
    
    if ((time >= breaks[0]) & (time<breaks[1])):
        return "00-02"
    elif ((time >= breaks[1]) & (time<breaks[2])):
        return "02-04"
    elif ((time >= breaks[2]) & (time<breaks[3])):
        return "04-06"
    elif ((time >= breaks[3]) & (time<breaks[4])):
        return "06-08"
    elif ((time >= breaks[4]) & (time<breaks[5])):
        return "08-10"
    elif ((time >= breaks[5]) & (time<breaks[6])):
        return "10-12"
    elif ((time >= breaks[6]) & (time<breaks[7])):
        return "12-14"
    elif ((time >= breaks[7]) & (time<breaks[8])):
        return "14-16"
    elif ((time >= breaks[8]) & (time<breaks[9])):
        return "16-18"
    elif ((time >= breaks[9]) & (time<breaks[10])):
        return "18-20"
    elif ((time >= breaks[10]) & (time<breaks[11])):
        return "20-22"
    else:
        return "22-24"
    
sf['Timegrp'] = sf['Time'].apply(timegrp)
temp=sf.groupby('Timegrp', agg.COUNT).sort('Timegrp')

# Create another column to index the Timegrp, which is needed later for the slider
def timegrp_index(time):
    
    if ((time == "00-02")):
        return 0
    elif ((time == "02-04")):
        return 1
    elif ((time == "04-06")):
        return 2
    elif ((time == "06-08")):
        return 3
    elif ((time == "08-10")):
        return 4
    elif ((time == "10-12")):
        return 5
    elif ((time == "12-14")):
        return 6
    elif ((time == "14-16")):
        return 7
    elif ((time == "16-18")):
        return 8
    elif ((time == "18-20")):
        return 9
    elif ((time == "20-22")):
        return 10
    else:
        return 11
    
sf['Timegrp_index'] = sf['Timegrp'].apply(timegrp_index)

key = ["GRAND THEFT FROM LOCKED AUTO", "PETTY THEFT FROM LOCKED AUTO"]
theft_auto = sf.filter_by(key, 'Descript')

theft_auto['Incident'] = 1

def daytonum(day):
    m = ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]
    d = {name:val for val, name in enumerate(m)}

    return(d[day])

theft_auto['Day_num'] = theft_auto['DayOfWeek'].apply(daytonum)
theft_auto = theft_auto.sort([('Timegrp', False), ('Day_num', True)])

dftat = theft_auto.to_dataframe()

In [41]:
# Prepare the plot
#
bar = Bar(dftat,
          values='Incident',
          label='Timegrp',
          agg='count',
          legend='top_left',
          title="Car Vandalism Reported by Time of Day in 2-hr Intervals",
          plot_width = 900, plot_height=600,
         )
output_notebook()
show(bar)

#output_reset()
#output_file('./output/car_breakin_reported_bytime.html')
#show(VBoxForm(bar))

BokehJS successfully loaded.

### The evenings have the highest car break-ins?

Here, the number of thefts is at its highest during the hours of 18:00 - 20:00, which is surprising as one would assume car break-ins tend to happen at night.  But clearly the data suggest otherwise.  

One caveat worth noting here is that the "time" used here is the time the incident was reported to the police, not the actual time the break-in occurred.  So a break-in that occurred during the middle of the night most likely won't be noticed and reported by the owner until he/she reachs the car in the morning.  Similarly, break-in during the day probably won't be noticed and reported until the owners reach the car, usually after getting off work, which is the most accessible explanation for the spike found at 18:00-20:00 hours.  

Regardless, the total number of incidents report from 08:00 to 20:00 is 2809, which is significantly higher than the 1612 reported from 20:00 to 08:00.

During the day, it is actually easier to observe what is in the car for the thieves.  

Now the question.  Does this distribution apply to different days of the week as well?

Let's see.

In [42]:
m = ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]
df2 = dftat.copy()
#df2 = dftat['Timegrp','DayOfWeek','Incident']
df2.to_csv('./df2.csv', columns=['Timegrp','DayOfWeek','Incident'])
df2['Day'] = pd.Categorical.from_array(df2.DayOfWeek).reorder_categories(m)

bar_grp = Bar(df2, 
        label='Timegrp', 
        values='Incident', 
        agg='count', 
        group=cat(columns=['Day'], sort=True),
        title="Car Break-in by Time Groups and Day of Week", 
        plot_width = 1000, plot_height=600,
        legend='top_left',
        tooltips=[('Day: ', '@Day')],
        color=color(columns=['Day'], sort=True, palette=Spectral10)
)

output_notebook()
show(bar_grp)

BokehJS successfully loaded.

### Slightly different pattern...

So, from this chart, we can infer the following observations:

1. The hours (22-24, 00-02) have notably higher incidents on Fridays, Saturday, and Sunday than other days of the week. And this is probably due to people going out on the weekends.  Since Thursdays are usually the "going-out" nights, we see the higher car break-ins during that period of time.

In [57]:
# Make the plot
theft_wkday = theft_auto.groupby(['DayOfWeek'],  {'Counts':gl.aggregate.COUNT()}).sort('Counts', ascending=False)
df3 = theft_wkday.to_dataframe()

bar3 = Bar(df3,
          values='Counts',
          label=cat('DayOfWeek', sort=False),
          title="Car Break-in's by Day of the Week",
          plot_width = 900, plot_height=600
         )

output_notebook()
show(bar3)

BokehJS successfully loaded.

## Q. But where are the most car break-ins occur?

In [16]:
# Preparing the plot
#

map_options = GMapOptions(
    lat=37.763, lng=-122.444, 
    map_type="roadmap", 
    zoom=13, 
    styles="""
[{"featureType":"administrative","elementType":"all","stylers":[{"visibility":"on"},{"lightness":33}]},{"featureType":"landscape","elementType":"all","stylers":[{"color":"#f2e5d4"}]},{"featureType":"poi.park","elementType":"geometry","stylers":[{"color":"#c5dac6"}]},{"featureType":"poi.park","elementType":"labels","stylers":[{"visibility":"on"},{"lightness":20}]},{"featureType":"road","elementType":"all","stylers":[{"lightness":20}]},{"featureType":"road.highway","elementType":"geometry","stylers":[{"color":"#c5c6c6"}]},{"featureType":"road.arterial","elementType":"geometry","stylers":[{"color":"#e4d7c6"}]},{"featureType":"road.local","elementType":"geometry","stylers":[{"color":"#fbfaf7"}]},{"featureType":"water","elementType":"all","stylers":[{"visibility":"on"},{"color":"#acbcc9"}]}]
""")

x_range = Range1d()
y_range = Range1d()

i = 0

# Prepping the GMapPlot
plot = GMapPlot(
    x_range=x_range, y_range=y_range,
    map_options=map_options,
    title='Reported Car Break-ins', plot_width=1000, plot_height=900,
)

# Data
days=['Sunday', 'Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday']


for day in days:
    temp = theft_auto[theft_auto['DayOfWeek'] == day]
    source = ColumnDataSource(
    data=dict(
        lat=temp['Y'],
        lon=temp['X']
    )
    )
    circle = Circle(x="lon", y="lat", size=3, fill_color=Spectral7[i], line_color=Spectral7[i])

    i = i+1
    plot.add_glyph(source, circle)
    
pan = PanTool()
wheel_zoom = WheelZoomTool()

plot.add_tools(pan, wheel_zoom)
output_notebook()
show(plot)

# also send it to an outputfile
#output_file('./output/car_breakins_all.html')
#show(VBoxForm(plot))

BokehJS successfully loaded.

### So...

First of all, the car break-ins are relatively mild in the western parts of the city (eg. Sunset, Richmond), which are predominantly residential.  The neighborhoods that have the higest incidents of car break-ins are Tenderloin and SOMA (Southern PD).  Tenderloin is the most NYC like neighborhood in SF, and it has a higher concentration of single resident occupancy (SRO) housing projects and is the rougher neighbohoods of SF.  SOMA (the Southern PD in our dataset), is somewhat similar to the Tenderloin but it is a neighborhood that has been (and still is) undergoing significant change in the past 15 years.  There are rough spots but it is also a busy commercial districts especially for for small tech start ups.  

Although both neighborhood have non-negligible residential use, compared to the western and central neighborhoods, they are still the area where people go to either make money or spend money.  They are also the neighborhoods that have a lot street and garage parkings.  And that implies high density and number of vehicles targets.

The combinations of:

1. large vehicle influx and outflux for non-residents
2. pockets of undesirable "blocks"

make these two areas more susceptible for opportuniistic vandalisms like car break-ins.

The other notable hot spots are along the water on the north east corner where you'll find popular tourist spots like the Embarcadero, Fisherman's Wharf, etc.  Tourists who are not acustomed to having to "prepare" the car as they exit are prime victims for car break-ins.

## Q.  Is there a notcieable spacial difference in car break-ins given the day of the week?

In [40]:
# Treat data from each day of the week as a seperate static plot.  With the dropdown select, we use the Callback to change the data source that is driving the plot.
# Because the data size is manageablely small, we can pass the datasets to the JS at once and switch between them on the client side without having to resort to the bokeh-server.
# This means that we need to build one data source for each day of the week that we have data for and are going to switch between using the dropdown. 
# We build them and add them to a dictionary sources that holds them under a key that is the name of the year preficed with a _.

df_theft_auto = theft_auto.to_dataframe()
df_theft_auto.to_csv('./df_theft_auto.csv', encoding='utf-8')

#xmax = theft_auto['X'].max()
#xmin = theft_auto['X'].min()
#ymax = theft_auto['Y'].max()
#ymin = theft_auto['Y'].min()
#xrange = [xmin, xmax]
#yrange = [ymin, ymax]
#xrange, yrange
#lengs=theft_auto['X'].count()
#theft_auto['color'] = np.random.randn(lengs)

days=['Sunday', 'Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday']
colors = [Purples9[0], Purples9[1], Purples9[2], Purples9[3], Spectral7[0], Spectral7[5], Spectral7[6]]

def day_color(day):
    if (day == days[0]):
        return 0
    elif (day == days[1]):
        return 1
    elif (day == days[2]):
        return 2
    elif (day == days[3]):
        return 3
    elif (day == days[4]):
        return 4
    elif (day == days[5]):
        return 5
    else:
        return 6

sources = {}
color = pd.DataFrame()

for day in days:
    i = day_color(day)

    record = df_theft_auto[df_theft_auto['DayOfWeek'] == day]
    record.loc[:,'color'] = colors[i]

    sources[day] = ColumnDataSource(record)
    
dictionary_of_sources = dict(zip([x for x in days], ['%s' % x for x in days]))
js_source_array = str(dictionary_of_sources).replace("'", "")

In [18]:
# ### Building the plot

from IPython.display import display, HTML

import pandas as pd

from jinja2 import Template

from bokeh.models import (
    ColumnDataSource, Plot, Circle, Range1d, 
    LinearAxis, HoverTool, Text,
    SingleIntervalTicker, Slider, CustomJS
)
from bokeh.plotting import vplot
from bokeh.resources import JSResources
from bokeh.embed import file_html
from bokeh.io import output_file, output_notebook, show, vform

#from data import process_data

map_options = GMapOptions(
    lat=37.763, lng=-122.444, 
    map_type="roadmap", 
    zoom=13, 
    styles="""
[{"featureType":"administrative","elementType":"all","stylers":[{"visibility":"on"},{"lightness":33}]},{"featureType":"landscape","elementType":"all","stylers":[{"color":"#f2e5d4"}]},{"featureType":"poi.park","elementType":"geometry","stylers":[{"color":"#c5dac6"}]},{"featureType":"poi.park","elementType":"labels","stylers":[{"visibility":"on"},{"lightness":20}]},{"featureType":"road","elementType":"all","stylers":[{"lightness":20}]},{"featureType":"road.highway","elementType":"geometry","stylers":[{"color":"#c5c6c6"}]},{"featureType":"road.arterial","elementType":"geometry","stylers":[{"color":"#e4d7c6"}]},{"featureType":"road.local","elementType":"geometry","stylers":[{"color":"#fbfaf7"}]},{"featureType":"water","elementType":"all","stylers":[{"visibility":"on"},{"color":"#acbcc9"}]}]
""")

x_range = Range1d()
y_range = Range1d()

i = 0

# Prepping the GMapPlot
plot = GMapPlot(
    x_range=x_range, y_range=y_range,
    map_options=map_options,
    title='Reported Car Break-ins', plot_width=1000, plot_height=900,
)

# Add the circle
renderer_source = sources['%s' % days[0]]

circle_glyph = Circle(
    x='X', y='Y', size=3,
    fill_color='color', fill_alpha=0.8, 
    line_color='color', line_width=0.5, line_alpha=0.5)
circle_renderer = plot.add_glyph(renderer_source, circle_glyph)

# Add the hover (only against the circle and not other plot elements)
tooltips = "@Descript"
plot.add_tools(HoverTool(tooltips=tooltips, renderers=[circle_renderer]))

In [19]:
"""
### Add the dropdown and callback

Last, but not least, we add the slider widget and the JS callback code which changes the data of the 
renderer_source (powering the bubbles / circles) and the data of the text_source (powering background text). 

After we've set() the `data` we need to trigger() a `change`. slider, renderer_source, text_source are all 
available because we add them as args to Callback.

It is the combination of `sources = %s % (js_source_array)` in the JS and `Callback(args=sources...)` that 
provides the ability to look-up, by year, the JS version of our python-made ColumnDataSource.## Slider

"""

from bokeh.models.widgets import Select

# Add the slider
code = """
    var day = select.get('value'),
        sources = %s,
        new_source_data = sources[day].get('data');
        renderer_source.set('data', new_source_data);
""" % js_source_array


callback = CustomJS(args=sources, code=code)
select = Select(title='Day', value="", callback=callback, name='select', options=days)

callback.args["renderer_source"] = renderer_source
callback.args["select"] = select

# Stick the plot and the slider together
output_notebook()
show(vform(select, plot))

#output_file('./output/car_breakins_by_day.html')
#show(vform(select,plot))

BokehJS successfully loaded.

### Lastly, the temporal vs spatial view of the car break-in locations by day of week

Here we can get a glimpse of how the car break-ins scatter across the city based on the day of the week.

The temporal vs. spatial display of the data is very interesting, although it is not that useful.  It's pretty cool to look at and it offers the users the chance to manipulate what they see.  But for our purpose, other than flickers of change from one day to another, it is difficult to conclude a pattern based on this display.